In [1]:

import pandas as pd
import numpy as np
import re
import string
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn import svm
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import cross_val_score, cross_val_predict, KFold
from sklearn.metrics  import confusion_matrix, classification_report
from sklearn import metrics
from sklearn import tree
import pickle

In [2]:
import sklearn

In [3]:
pd.set_option('display.max_columns',None)
pd.set_option('display.max_rows',None)
pd.set_option('display.max_colwidth',-6)

C:\Users\ibrahim\Anaconda3\lib\site-packages\ipykernel_launcher.py:3: FutureWarning: Passing a negative integer is deprecated in version 1.0 and will not be supported in future version. Instead, use None to not limit the column width.
  This is separate from the ipykernel package so we can avoid doing imports until


In [4]:

data_df=pd.read_excel("trining set.xlsx")


In [5]:
data_df.head()

Unnamed: 0                          name  \
0  0           مشاعل #الزعيم_العالمي_الملكي   
1  1           Abureem                        
2  2           ُBo riyad ... ♚                
3  3           إبراهيم الملحم                 
4  4           Different                      

                                                                                                                                          text  \
0  إعلان واطي من سكشن-بي 😐😑😏 https://t.co/uKArk6lg5k                                                                                             
1  @shrimpshacksa للأسف كانت تجربة سيئة معكم امس وماكنت متوقع تنزلون الى هذا المستوى طلبت جامبو دبل ولما وصلت البيت كانت فقط ٤ حبات جامبو؟؟؟؟    
2  RT @Mur_Hus: @Saad_Maestro @MaestroPizzaKSA @lc_saudi @DominosKSA @PizzaHut_Saudi @alsaheer3 المفروض سميكة لكن جاني 4 حبات سميكة و14 رقيقة…   
3  @SubwaySaudi آخر مرة بإذن الله اشتري منكم ، كل يوم زيادة بالاسعار ، ما فيه ذرة احترام للعميل ، كنت زبون دائم عندكم… https://t.co/TcWy2poBwR   
4  اليوم بروح سكشن بي منقبة عناد                                                                                                                 

  Stance  
0  neg    
1  neg    
2  neg    
3  neg    
4  neg

In [6]:
data_df=data_df[['name','text','Stance']]

In [7]:
data_df.Stance.value_counts()

neu    1839
neg    952 
pos    952 
Name: Stance, dtype: int64

In [8]:
data_df[data_df["Stance"]=='pos'].count()

name      952
text      952
Stance    952
dtype: int64

In [9]:
# remove punctuations علامات الترقيم  

arabic_punctuations = '''`÷×؛<>()*&^%][ـ،/:"؟.,'{}~¦+|!”…“–ـ'''
english_punctuations = string.punctuation
punctuations_list = arabic_punctuations + english_punctuations

def remove_punctuations(text):
    translator = str.maketrans('', '', punctuations_list)
    return text.translate(translator)

In [10]:
def normalize_arabic(text):
    text = re.sub("[إأآا]", "ا", text)
    text = re.sub("ى", "ي", text)
    text = re.sub("_"," ", text)
    text = re.sub("ة", "ه", text)
    text = re.sub("گ", "ك", text)
    return text

In [11]:
# remove repeated letters
def remove_repeating_char(text):
    return re.sub(r'(.)\1+', r'\1', text)

In [12]:
#start processing the tweet
def processPost(tweet):

    #Replace @username with empty string
    tweet = re.sub('@[^\s]+', ' ', tweet)
    
    #Convert www.* or https?://* to " "
    tweet = re.sub('((www\.[^\s]+)|(https?://[^\s]+))',' ',tweet)
    
    #Replace #word with word
    tweet = re.sub(r'#([^\s]+)', r'\1', tweet)
    
    # normalize the tweet
    tweet= normalize_arabic(tweet)

    # remove punctuations
    tweet= remove_punctuations(tweet)

    
    # remove repeated letters
    tweet=remove_repeating_char(tweet)
    
    return tweet

In [13]:
data_df["clean text"] = data_df['text'].apply(lambda x: processPost(x))

In [14]:
data_df.head()

name  \
0  مشاعل #الزعيم_العالمي_الملكي   
1  Abureem                        
2  ُBo riyad ... ♚                
3  إبراهيم الملحم                 
4  Different                      

                                                                                                                                          text  \
0  إعلان واطي من سكشن-بي 😐😑😏 https://t.co/uKArk6lg5k                                                                                             
1  @shrimpshacksa للأسف كانت تجربة سيئة معكم امس وماكنت متوقع تنزلون الى هذا المستوى طلبت جامبو دبل ولما وصلت البيت كانت فقط ٤ حبات جامبو؟؟؟؟    
2  RT @Mur_Hus: @Saad_Maestro @MaestroPizzaKSA @lc_saudi @DominosKSA @PizzaHut_Saudi @alsaheer3 المفروض سميكة لكن جاني 4 حبات سميكة و14 رقيقة…   
3  @SubwaySaudi آخر مرة بإذن الله اشتري منكم ، كل يوم زيادة بالاسعار ، ما فيه ذرة احترام للعميل ، كنت زبون دائم عندكم… https://t.co/TcWy2poBwR   
4  اليوم بروح سكشن بي منقبة عناد                                                                                                                 

  Stance  \
0  neg     
1  neg     
2  neg     
3  neg     
4  neg     

                                                                                                                clean text  
0  اعلان واطي من سكشنبي 😐😑😏                                                                                                 
1   لاسف كانت تجربه سيئه معكم امس وماكنت متوقع تنزلون الي هذا المستوي طلبت جامبو دبل ولما وصلت البيت كانت فقط ٤ حبات جامبو  
2  RT المفروض سميكه لكن جاني 4 حبات سميكه و14 رقيقه                                                                         
3   اخر مره باذن اله اشتري منكم كل يوم زياده بالاسعار ما فيه ذره احترام لعميل كنت زبون دائم عندكم                           
4  اليوم بروح سكشن بي منقبه عناد

In [15]:
data_df.head(4000)

name  \
0     مشاعل #الزعيم_العالمي_الملكي                        
1     Abureem                                             
2     ُBo riyad ... ♚                                     
3     إبراهيم الملحم                                      
4     Different                                           
5     Abeer                                               
6     just me                                             
7     رؤى السريحي                                         
8     just me                                             
9     ☆•° نجمة                                            
10    عمر الروقي                                          
11    ✨إيمان✨                                             
12    Eme katan                                           
13    الحمدلله                                            
14    gasq                                                
15    Mashaell                                            
16    نوره.                                               
17    عو 👻                                                
18    م                                                   
19    Mishal M Alismail                                   
20    Faisal148                                           
21    A                                                   
22    Mashaell                                            
23    بـْـــ س                                            
24    SнirEEŋo                                            
25    Miami 👩🏻‍🎓                                          
26    Ayman Almezher                                      
27    Ayman Almezher                                      
28    Shahd cherry🍒7                                      
29    baraa mohammad                                      
30    baraa mohammad                                      
31    عبدالرحيم                                           
32    رامي                                                
33    سعودي وافتخر اللهم احمي مملكتنا الحبيبة من كل شر    
34    سعودي وافتخر اللهم احمي مملكتنا الحبيبة من كل شر    
35    فيصل من غير شك ✨🦌                                   
36    فيصل من غير شك ✨🦌                                   
37    فيصل من غير شك ✨🦌                                   
38    فيصل من غير شك ✨🦌                                   
39    ثامر                                                
40    Adel                                                
41    ђยรรค๓                                              
42    Mohammed                                            
43    Asy                                                 
44    ᕼᗩᔕᔕᗩᑎ #CFC                                         
45    Pseudo Beeks                                        
46    سنيك                                                
47    happy.m                                             
48    happy.m                                             
49    Staisal                                             
50    LU____ALRUBIAN🎶                                     
51    Nassr                                               
52    نوف السهو                                           
53    Shahad_O                                            
54    F                                                   
55    F                                                   
56    ﮼فهدة،بنت،عبدالعزيز                                 
57    Abdulrahman 🍃                                       
58    صـالـح بن راشـد                                     
59    Mohammed J. Baidas                                  
60    Mohammed J. Baidas                                  
61    ِ                                                   
62    King                                                
63    نــوآل الشمري #سلمان🇸🇦                              
64    id4abunawaf@                                        
65    Felz                                                
66    MaGeD,sa                                            
67    لـمى.                            

In [16]:
# remove the "Neutral" class
data_df=data_df[data_df['Stance'] != "neu"]

In [17]:
data_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1904 entries, 0 to 3742
Data columns (total 4 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   name        1904 non-null   object
 1   text        1904 non-null   object
 2   Stance      1904 non-null   object
 3   clean text  1904 non-null   object
dtypes: object(4)
memory usage: 74.4+ KB


In [18]:
data_df[data_df['Stance'] == "neg"].count()

name          952
text          952
Stance        952
clean text    952
dtype: int64

In [19]:
data_df[data_df['Stance'] == "pos"].count()

name          952
text          952
Stance        952
clean text    952
dtype: int64

In [20]:
data_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1904 entries, 0 to 3742
Data columns (total 4 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   name        1904 non-null   object
 1   text        1904 non-null   object
 2   Stance      1904 non-null   object
 3   clean text  1904 non-null   object
dtypes: object(4)
memory usage: 74.4+ KB


In [21]:
data_df['Stance'] = data_df['Stance'].map({'pos': 1, 'neg': 0}) 

In [22]:
data= data_df['clean text']
target= data_df['Stance']

In [23]:
target

0       0
1       0
2       0
3       0
4       0
5       0
6       0
7       0
8       0
9       0
10      0
11      0
12      0
13      0
14      0
15      0
16      0
17      0
18      0
19      0
20      0
21      0
22      0
23      0
24      0
25      0
26      0
27      0
28      0
29      0
30      0
31      0
32      0
33      0
34      0
35      0
36      0
37      0
38      0
39      0
40      0
41      0
42      0
43      0
44      0
45      0
46      0
47      0
48      0
49      0
50      0
51      0
52      0
53      0
54      0
55      0
56      0
57      0
58      0
59      0
60      0
61      0
62      0
63      0
64      0
65      0
66      0
67      0
68      0
69      0
70      0
71      0
72      0
73      0
74      0
75      0
76      0
77      0
78      0
79      0
80      0
81      0
82      0
83      0
84      0
85      0
86      0
87      0
88      0
89      0
90      0
91      0
92      0
93      0
94      0
95      0
96      0
97      0
98      0
99      0


In [24]:
# Use TfidfVectorizer for feature extraction (TFIDF to convert textual data to numeric form):
tf_vec = TfidfVectorizer()
X = tf_vec.fit_transform(data)

In [25]:
len(tf_vec.vocabulary_)

4346

In [26]:
tf_vec.vocabulary_

{'اعلان': 1333,
 'واطي': 3736,
 'من': 3539,
 'سكشنبي': 2744,
 'لاسف': 3201,
 'كانت': 3127,
 'تجربه': 2228,
 'سيئه': 2783,
 'معكم': 3512,
 'امس': 1883,
 'وماكنت': 4088,
 'متوقع': 3410,
 'تنزلون': 2368,
 'الي': 1873,
 'هذا': 3671,
 'المستوي': 1781,
 'طلبت': 2893,
 'جامبو': 2402,
 'دبل': 2569,
 'ولما': 4075,
 'وصلت': 3987,
 'البيت': 1455,
 'فقط': 3047,
 'حبات': 2473,
 'rt': 837,
 'المفروض': 1799,
 'سميكه': 2763,
 'لكن': 3271,
 'جاني': 2407,
 'و14': 3690,
 'رقيقه': 2653,
 'اخر': 1214,
 'مره': 3462,
 'باذن': 1962,
 'اله': 1849,
 'اشتري': 1283,
 'منكم': 3558,
 'كل': 3151,
 'يوم': 4314,
 'زياده': 2688,
 'بالاسعار': 1982,
 'ما': 3308,
 'فيه': 3068,
 'ذره': 2598,
 'احترام': 1192,
 'لعميل': 3263,
 'كنت': 3174,
 'زبون': 2678,
 'دائم': 2564,
 'عندكم': 2973,
 'اليوم': 1876,
 'بروح': 2092,
 'سكشن': 2743,
 'بي': 2180,
 'منقبه': 3556,
 'عناد': 2970,
 'وانا': 3833,
 'تفاجات': 2323,
 'بسعر': 2110,
 'ساندويتشين': 2717,
 'ب٧١': 2210,
 'ريال': 2666,
 'وبدون': 3845,
 'مشروب': 3480,
 'بعد': 2134,
 'ليش': 330

In [27]:
pickle.dump(tf_vec.vocabulary_, open("feature.pickel","wb"))#extract the featurs

In [28]:
X_train, X_test, y_train, y_test = train_test_split(X, target, test_size=0.5, random_state=42)

In [30]:
# create the classifer and fit the training data and lables
classifier_svm = svm.SVC(kernel='linear', C=1)
classifier_svm.fit(X_train,y_train)
print("SVM accuracy: %.2f"%classifier_svm.score(X_test, y_test))

#do a 2 fold cross-validation 
results_svm = cross_val_score(classifier_svm, X,target, cv=2)
print("\n2-fold cross-validation:")
print(results_svm)

print("The average accuracy of the SVM classifier is : %.2f" % np.mean(results_svm))

print("\nConfusion matrix of the SVM classifier:")
predicted_svm = classifier_svm.predict(X_test)
print(confusion_matrix(y_test,predicted_svm))


print("\nClassification_report of SVM classifier:")
print(classification_report(y_test,predicted_svm))
print("----------------------------------------------------------------------------")

SVM accuracy: 0.88

2-fold cross-validation:
[0.82457983 0.81827731]
The average accuracy of the SVM classifier is : 0.82

Confusion matrix of the SVM classifier:
[[435  43]
 [ 74 400]]

Classification_report of SVM classifier:
              precision    recall  f1-score   support

           0       0.85      0.91      0.88       478
           1       0.90      0.84      0.87       474

    accuracy                           0.88       952
   macro avg       0.88      0.88      0.88       952
weighted avg       0.88      0.88      0.88       952

----------------------------------------------------------------------------


In [31]:
classifier_log =  LogisticRegression().fit(X_train,y_train)

In [32]:
print("Logisitic Accuracy: %.2F"%classifier_log.score(X_test, y_test))
results_log = cross_val_score(classifier_log, X,target, cv=2)


print("\n2-fold cross-validation:")
print(results_log)


print("The average accuracy of the Logisitic classifier is : %.2f" % np.mean(results_log))
print("\nConfusion matrix of the Logisitic classifier:")
predicted_log= classifier_log.predict(X_test)
print(confusion_matrix(y_test,predicted_log))


print("\nClassification_report of Logisitic classifier:")
print(classification_report(y_test,predicted_log))
print("----------------------------------------------------------------------------")

Logisitic Accuracy: 0.84

2-fold cross-validation:
[0.78361345 0.78676471]
The average accuracy of the Logisitic classifier is : 0.79

Confusion matrix of the Logisitic classifier:
[[430  48]
 [107 367]]

Classification_report of Logisitic classifier:
              precision    recall  f1-score   support

           0       0.80      0.90      0.85       478
           1       0.88      0.77      0.83       474

    accuracy                           0.84       952
   macro avg       0.84      0.84      0.84       952
weighted avg       0.84      0.84      0.84       952

----------------------------------------------------------------------------


In [33]:
classifier_DT=tree.DecisionTreeClassifier().fit(X_train,y_train)
print("Tree Decision Accuracy: %.2F"%classifier_DT.score(X_test, y_test))
results_DT = cross_val_score(classifier_DT, X,target, cv=2)


print("\n2-fold cross-validation:")
print(results_DT)


print("The average accuracy of the Decision Tree Classifier is : %.2f" % np.mean(results_DT))
print("\nConfusion matrix of the Decision Tree Classifier:")
predicted_DT= classifier_DT.predict(X_test)
print(confusion_matrix(y_test,predicted_DT))


print("\nClassification_report of Logisitic classifier:")
print(classification_report(y_test,predicted_DT))
print("----------------------------------------------------------------------------")

Tree Decision Accuracy: 0.83

2-fold cross-validation:
[0.82352941 0.91596639]
The average accuracy of the Decision Tree Classifier is : 0.87

Confusion matrix of the Decision Tree Classifier:
[[408  70]
 [ 96 378]]

Classification_report of Logisitic classifier:
              precision    recall  f1-score   support

           0       0.81      0.85      0.83       478
           1       0.84      0.80      0.82       474

    accuracy                           0.83       952
   macro avg       0.83      0.83      0.83       952
weighted avg       0.83      0.83      0.83       952

----------------------------------------------------------------------------


In [102]:
df=pd.read_excel("C:/Users/ibrahim/Desktop/Gp1/foursqare/remin_rest.xlsx")

In [71]:
df[df["clean text"].isnull()==True]

Empty DataFrame
Columns: [resturant, userName, Date, text, Photo, test, rate, countOfrate, Day, clean Name, gender, clean text, Stance]
Index: []

In [72]:
df.drop(df[df["clean text"].isnull()==True].index,inplace=True)

In [73]:
data=df['clean text']

In [74]:
len(data)

1478

In [75]:
transformer = TfidfVectorizer(vocabulary=pickle.load(open("feature.pickel","rb")))# load the featurs to predict the rimaing data set

In [76]:
transformer.vocabulary

{'اعلان': 1333,
 'واطي': 3736,
 'من': 3539,
 'سكشنبي': 2744,
 'لاسف': 3201,
 'كانت': 3127,
 'تجربه': 2228,
 'سيئه': 2783,
 'معكم': 3512,
 'امس': 1883,
 'وماكنت': 4088,
 'متوقع': 3410,
 'تنزلون': 2368,
 'الي': 1873,
 'هذا': 3671,
 'المستوي': 1781,
 'طلبت': 2893,
 'جامبو': 2402,
 'دبل': 2569,
 'ولما': 4075,
 'وصلت': 3987,
 'البيت': 1455,
 'فقط': 3047,
 'حبات': 2473,
 'rt': 837,
 'المفروض': 1799,
 'سميكه': 2763,
 'لكن': 3271,
 'جاني': 2407,
 'و14': 3690,
 'رقيقه': 2653,
 'اخر': 1214,
 'مره': 3462,
 'باذن': 1962,
 'اله': 1849,
 'اشتري': 1283,
 'منكم': 3558,
 'كل': 3151,
 'يوم': 4314,
 'زياده': 2688,
 'بالاسعار': 1982,
 'ما': 3308,
 'فيه': 3068,
 'ذره': 2598,
 'احترام': 1192,
 'لعميل': 3263,
 'كنت': 3174,
 'زبون': 2678,
 'دائم': 2564,
 'عندكم': 2973,
 'اليوم': 1876,
 'بروح': 2092,
 'سكشن': 2743,
 'بي': 2180,
 'منقبه': 3556,
 'عناد': 2970,
 'وانا': 3833,
 'تفاجات': 2323,
 'بسعر': 2110,
 'ساندويتشين': 2717,
 'ب٧١': 2210,
 'ريال': 2666,
 'وبدون': 3845,
 'مشروب': 3480,
 'بعد': 2134,
 'ليش': 330

In [77]:
p=transformer.fit_transform(data)

In [78]:
predict=classifier_svm.predict(p)

In [79]:
df["Stance"]=predict

In [81]:
df.head(500)

resturant                          userName        Date  \
0    mama noura  Yazeed Althobaiti                 2020-11-03   
1    mama noura  S A                               2020-10-03   
2    mama noura  Abdulrahman M                     2020-11-03   
3    mama noura  Fooder                            2020-05-03   
4    mama noura  Faleh Alsuhaimi                   2020-02-27   
5    mama noura  Mishary                           2020-01-22   
6    mama noura  Sadeem A.                         2020-06-03   
7    mama noura  aalmarshad                        2019-07-29   
8    mama noura  Hod                               2019-08-17   
9    mama noura  Hanan                             2020-05-01   
10   mama noura  Faisal 🌟                          2020-01-21   
11   mama noura  Bayan Khalid                      2019-07-25   
12   mama noura  Mr connoisseur                    2019-02-10   
13   mama noura  القعقاع التميمي                   2019-07-29   
14   mama noura  Sondos SM                         2020-02-27   
15   mama noura  Malak Alshammari                  2019-10-11   
16   mama noura  A7mad ✨                           2020-01-23   
17   mama noura  Im Person                         2020-02-27   
18   mama noura  Abdulkarim                        2019-10-16   
19   mama noura  Fares DD                          2020-01-20   
20   mama noura  Kemo Kemo                         2020-01-02   
21   mama noura  Mohammed .                        2020-08-02   
22   mama noura  Abduulah Almuhaidib               2019-07-30   
23   mama noura  ذيب نجد                           2019-07-30   
24   mama noura  MAQ                               2019-08-31   
25   mama noura  Azzam                             2019-07-28   
26   mama noura  Shawarma Lover                    2019-11-27   
27   mama noura  Mohammed Alhagbani                2019-08-24   
28   mama noura  Khulood                           2020-01-13   
29   mama noura  Lina                              2019-12-24   
30   mama noura  Haifa .                           2019-08-24   
31   mama noura  Hamad Altuwaijri                  2019-12-14   
32   mama noura  Gökhan Bal                        2019-01-12   
33   mama noura  Haifa .                           2019-08-24   
34   mama noura  Abo Kharem                        2019-06-09   
35   mama noura  shahd mohamad                     2019-10-16   
36   mama noura  T S T                             2019-12-18   
37   mama noura  Lamia                             2019-07-16   
38   mama noura  Rami Bakhsh ⚡                     2019-12-20   
39   mama noura  Majed Alashari                    2019-11-30   
40   mama noura  Reem                              2019-09-09   
41   mama noura  R|رَ                              2020-01-14   
42   mama noura  Yasser Alamri                     2019-10-16   
43   mama noura  فُهيد بِن عبدالرحمَن 🎻            2019-10-19   
44   mama noura  Sergen Bilgın                     2020-05-03   
45   mama noura  RANA                              2020-06-03   
46   mama noura  Naif Hwaymel                      2019-09-26   
47   mama noura  Sara Ahmed                        2020-05-03   
48   mama noura  Sara 🎀🧸                           2019-04-12   
49   mama noura  Lulu Alshaygy                     2019-10-21   
50   mama noura  Nasser Abdullah                   2019-04-10   
51   mama noura  Moataz Abdullah                   2019-11-27   
52   mama noura  Bader bin Abdulaziz               2019-09-19   
53   mama noura  Tama'9r                           2019-02-09   
54   mama noura  شعاع                              2019-10-09   
55   mama noura  فهد ..                            2019-08-21   
56   mama noura  Bader Bood                        2019-12-14   
57   mama noura  Abdulaziz Bin Abdullah Almousa    2019-07-09   
58   mama noura  Lulu Alshaygy                     2019-10-21   
59   mama noura  عيسى العنزي                       2019-12-17   
60   mama noura  Manssoor AlRaee         

In [82]:
df.Stance.value_counts()

1    1084
0    394 
Name: Stance, dtype: int64

In [83]:
df['Stance'] = df['Stance'].map({1:'pos',0:'neg'}) #map all neg =0 all pos==1

In [84]:
df.Stance.value_counts()

pos    1084
neg    394 
Name: Stance, dtype: int64